In [2]:
import os
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset
from torchvision import transforms
import random
from PIL import Image, ImageDraw, ImageFont, ImageOps, ImageFilter
import cv2
import numpy as np

DATASET_DIR = "dataset"
SAVE_PATH = "best_model_8.pth"
BATCH_SIZE = 32
EPOCHS = 30
LEARNING_RATE = 0.001
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

CLASSES = "ABEKMHOPCTYX0123456789"
NUM_CLASSES = len(CLASSES)
CLASS_TO_IDX = {char: idx for idx, char in enumerate(CLASSES)}
IDX_TO_CLASS = {idx: char for char, idx in CLASS_TO_IDX.items()}

In [ ]:

FONT_PATH = "RoadNumbers2.0.ttf"
CONFIG_FILE = "dataset_config.txt"

# Буквы и цифры, используемые в российских номерах
SYMBOLS = "ABEKMHOPCTYX0123456789"
SMALL_FONT_SIZES = [26, 32]  # Размеры шрифта с уменьшенным блюром
IMG_SIZE = (28, 28)
FONT_SIZES = [26, 32, 38, 46, 54, 58]
MAX_ROTATION = 15
AUGMENTATIONS = 240

os.makedirs(DATASET_DIR, exist_ok=True)

try:
    font = ImageFont.truetype(FONT_PATH, FONT_SIZES[0])
except IOError:
    print(f"Шрифт {FONT_PATH} не найден. Убедитесь, что он находится в текущей директории.")
    exit()

def expand_characters(img, kernel_size=(2, 2), iterations=1):
    kernel = cv2.getStructuringElement(cv2.MORPH_RECT, kernel_size)
    img_array = np.array(img)
    expanded = cv2.dilate(img_array, kernel, iterations=iterations)
    return Image.fromarray(expanded)

def add_random_gaps(img, num_gaps=5, gap_size=5):
    draw = ImageDraw.Draw(img)
    for _ in range(num_gaps):
        x1 = random.randint(0, IMG_SIZE[0] - gap_size)
        y1 = random.randint(0, IMG_SIZE[1] - gap_size)
        x2 = x1 + gap_size
        y2 = y1 + gap_size
        draw.rectangle([x1, y1, x2, y2], fill=255) 
    return img

def apply_blur(img, blur_limits=None):
    if blur_limits is None:
        blur_limits = {"box": 4, "gaussian": 3, "motion": 8}

    blur_type = random.choice(["box", "gaussian", "motion"])

    if blur_type == "box":
        radius = random.randint(1, blur_limits["box"])
        img = img.filter(ImageFilter.BoxBlur(radius))
    elif blur_type == "gaussian":
        radius = random.randint(1, blur_limits["gaussian"])
        img = img.filter(ImageFilter.GaussianBlur(radius))
    elif blur_type == "motion":
        kernel_size = random.randint(4, blur_limits["motion"])
        kernel_motion_blur = np.zeros((kernel_size, kernel_size))
        kernel_motion_blur[int((kernel_size - 1) / 2), :] = 1
        kernel_motion_blur /= kernel_size
        img_array = cv2.filter2D(np.array(img), -1, kernel_motion_blur)
        img = Image.fromarray(img_array)
    return img

def add_noise(img, intensity=30):
    img_array = np.array(img)
    noise = np.random.normal(0, intensity, img_array.shape).astype(np.int32)
    noisy_img = np.clip(img_array + noise, 0, 255).astype(np.uint8)
    return Image.fromarray(noisy_img)

def shift_image(img, max_shift=4):
    """
    Сдвигает изображение на случайное количество пикселей по осям X и Y.

    :param img: PIL Image объект.
    :param max_shift: Максимальное смещение в пикселях по каждой оси.
    :return: Сдвинутое изображение.
    """
    x_shift = random.randint(-max_shift, max_shift)
    y_shift = random.randint(-max_shift, max_shift)
    return img.transform(
        img.size,
        Image.AFFINE,
        (1, 0, x_shift, 0, 1, y_shift),
        fillcolor=255
    )

def create_augmentations(symbol, font_sizes, max_rotation, augmentations, config_lines):
    for i in range(augmentations):
        for font_size in font_sizes:
            current_font = ImageFont.truetype(FONT_PATH, font_size)

            # Создаём пустое изображение с белым фоном
            img = Image.new("L", IMG_SIZE, 255)
            draw = ImageDraw.Draw(img)

            # Получаем размеры текста с использованием Font.getbbox
            text_bbox = draw.textbbox((0, 0), symbol, font=current_font)
            text_width, text_height = text_bbox[2] - text_bbox[0], text_bbox[3] - text_bbox[1]

            # Рассчитываем координаты для центрирования текста
            x = (IMG_SIZE[0] - text_width) // 2 - text_bbox[0]
            y = (IMG_SIZE[1] - text_height) // 2 - text_bbox[1]

            # Рисуем текст
            draw.text((x, y), symbol, font=current_font, fill=0)

            # Для первого прогона символа с данным размером шрифта сохраняем без аугментаций
            if i == 0:
                symbol_dir = os.path.join(DATASET_DIR, symbol)
                os.makedirs(symbol_dir, exist_ok=True)
                file_path = os.path.join(symbol_dir, f"{symbol}_{font_size}_{i}.png")
                img.save(file_path)

                config_lines.append(f"{file_path},{symbol}\n")
                continue

            # Случайное смещение символа
            if random.random() < 0.7: 
                img = shift_image(img, max_shift=4)

            # Случайный поворот изображения
            rotation = random.uniform(-max_rotation, max_rotation)
            img = img.rotate(rotation, expand=False, fillcolor=255)

            # Случайное расширение символов
            if random.random() < 0.5:
                kernel_size = (random.randint(1, 2), random.randint(1, 2))
                iterations = 1
                img = expand_characters(img, kernel_size=kernel_size, iterations=iterations)

            # Случайное добавление разрывов
            if random.random() < 0.15:
                num_gaps = random.randint(1, 5)
                gap_size = random.randint(2, 4)
                img = add_random_gaps(img, num_gaps=num_gaps, gap_size=gap_size)

            # Инверсия цветов с вероятностью 25%
            if random.random() < 0.15:
                img = ImageOps.invert(img)

            # Определяем лимиты блюра в зависимости от размера шрифта
            if font_size in SMALL_FONT_SIZES:
                blur_limits = {"box": 2, "gaussian": 1, "motion": 6}  # Уменьшенные лимиты
            else:
                blur_limits = {"box": 4, "gaussian": 3, "motion": 8}  # Оригинальные лимиты

            # Случайное добавление блюра
            if random.random() < 0.85:
                img = apply_blur(img, blur_limits=blur_limits)

            # Случайное добавление шума
            if random.random() < 0.1:
                noise_intensity = random.randint(10, 20)
                img = add_noise(img, intensity=noise_intensity)

            # Сохраняем изображение
            symbol_dir = os.path.join(DATASET_DIR, symbol)
            os.makedirs(symbol_dir, exist_ok=True)
            file_path = os.path.join(symbol_dir, f"{symbol}_{font_size}_{i}.png")
            img.save(file_path)

            config_lines.append(f"{file_path},{symbol}\n")

def main():
    config_lines = []

    for symbol in SYMBOLS:
        create_augmentations(symbol, FONT_SIZES, MAX_ROTATION, AUGMENTATIONS, config_lines)

    config_path = os.path.join(DATASET_DIR, CONFIG_FILE)
    with open(config_path, "w") as config:
        config.writelines(config_lines)

    print(f"Датасет сохранен в папке '{DATASET_DIR}'.")
    print(f"Конфигурационный файл создан: {CONFIG_FILE}")

if __name__ == "__main__":
    main()


Датасет сохранен в папке 'dataset'.
Конфигурационный файл создан: dataset_config.txt
